En este notebook se analiza los datos y se muestran los resultados. La explicación del problema está en ***README.md*** y el código que genera la predicción en ***app.py***.

# 0. Importaciones e ingesta de datos

In [99]:
import os

import pandas as pd
from sklearn.manifold import TSNE
from statistics import variance
import plotly.express as px

from sklearn.ensemble import RandomForestClassifier

import warnings
warnings.filterwarnings('ignore')

ROOT=os.getcwd()
TRAIN_FILE=os.path.join(ROOT,'train.csv')
TEST_FILE=os.path.join(ROOT,'test.csv')
PRED_CSV_FILE=os.path.join(ROOT,'predictions.csv')
CV_RES_FILE=os.path.join(ROOT,'cv_results.csv')

train=pd.read_csv(TRAIN_FILE, sep=';')
X_train=train.drop('target',axis=1)
y_train=train['target']

X_test=pd.read_csv(TEST_FILE, sep=';') # Para el conjutno de prueba solo tenemos las características.

# 1. Visualización de datos

## 1.1 Primer vistazo

Primero observamos el dataset para comprender su estructura.

In [5]:
train

feature1  feature2  feature3  feature4  feature5  feature6  feature7  \
0    -0.458258 -0.579012  2.886009 -0.075516  1.674060 -2.431912  0.534850   
1     1.626615 -0.028332 -1.443184 -1.007447 -0.989093  1.202627 -0.038211   
2     1.721356 -0.137676 -1.322593 -1.333187 -0.723713  0.843285 -0.588495   
3    -0.715103  3.265915 -0.791030 -2.967881  2.497628 -0.277387 -0.551611   
4     2.944098  0.197871 -2.257025  1.032789 -4.104693  4.716115 -0.380813   
...        ...       ...       ...       ...       ...       ...       ...   
2095 -1.490976  0.710351  0.563602  0.819782  0.622330 -0.260162 -0.430694   
2096 -1.100961  1.503310  0.389692  1.120231 -0.069433  1.037263  2.128583   
2097 -0.049519  1.334648  1.389703 -1.695882  1.967512 -1.252090 -0.529434   
2098  0.872172 -2.125563 -1.142489  0.743429 -1.616948  0.345578 -0.357935   
2099  0.051488 -0.743062 -1.147962 -0.969209  0.366257 -0.782323  0.160630   

      feature8  target  
0    -0.846473       2  
1    -1.298616       0  
2     0.066682       0  
3     0.668354       2  
4    -1.393825       0  
...        ...     ...  
2095  1.674863       0  
2096  0.385863       0  
2097 -2.322296       2  
2098 -0.814865       2  
2099 -0.452189       1  

[2100 rows x 9 columns]

In [7]:
X_test

feature1  feature2  feature3  feature4  feature5  feature6  feature7  \
0    0.052199  2.514513 -0.197672  1.978709 -2.014691  3.852886 -2.126254   
1   -0.828073  0.085895  1.712522  0.078828  1.280057 -1.462486  2.469702   
2   -1.086411 -0.142109  0.013089 -0.115223  0.948242 -1.121574  0.517415   
3    0.093129  2.868934 -0.075120  0.650641 -0.886186  2.917352 -0.722935   
4    0.046167  2.822612  0.433869 -3.054525  2.537684 -0.717312  0.862266   
..        ...       ...       ...       ...       ...       ...       ...   
895 -0.744054 -0.243469 -0.976395 -0.668870  0.751827 -0.880680 -1.515322   
896 -1.589089 -0.855138  0.551648  1.194362  0.495606 -1.215525 -0.989431   
897 -1.531395  1.379523  0.385277 -1.116332  2.182242 -1.399055 -0.063682   
898  0.942801 -1.930453  0.433113  0.552354 -0.861105 -0.452670 -2.629706   
899 -0.092229 -0.009093  2.485497 -0.422361  1.476970 -1.781184 -0.957777   

     feature8  
0    0.794624  
1    0.816540  
2    0.250672  
3    0.063071  
4   -0.525491  
..        ...  
895 -0.611073  
896 -1.497979  
897  2.430342  
898 -1.239662  
899 -1.496381  

[900 rows x 8 columns]

Efectivamente se trata de 8 características numéricas + una etiqueta, presente en el conjunto de entrenamiento pero no de prueba.

A continuación observamos si existen datos nulos.

In [16]:
train.count()

feature1    2100
feature2    2100
feature3    2100
feature4    2100
feature5    2100
feature6    2100
feature7    2100
feature8    2100
target      2100
dtype: int64

In [17]:
X_test.count()

feature1    900
feature2    900
feature3    900
feature4    900
feature5    900
feature6    900
feature7    900
feature8    900
dtype: int64

Los 2 conjuntos están limpios. Finalmente comprovamos si el conjunto de prueba está equilibrado.

In [18]:
y_train.value_counts()

0    713
1    705
2    682
Name: target, dtype: int64

El desequilibrio de muestras es leve, aunque la cantidad de muestras de calidad de aire 2 (mala) es algo inferior al resto.

## 1.2 Visualización de la distribución de los datos

En primer lugar vamos a proyectar el conjunto de entrenamiento en 3D usando el algoritmo [t-SNE](https://en.wikipedia.org/wiki/T-distributed_stochastic_neighbor_embedding) junto a las etiquetas que le corresponden.

In [52]:
to3d=TSNE(n_components=3)

train3d=pd.DataFrame(to3d.fit_transform(X_train),columns=['x','y','z'])
train3d['target']=y_train.astype(str)

train3dplot=px.scatter_3d(train3d,x='x',y='y',z='z',color='target',category_orders={'target':['0','1','2']})

train3dplot

Podemos observar que cada categoría tiene un cluster asociado, aunque parte de esos clusters se intersectan con los demás, así que los puntos en esas intersecciones pueden ser más difíciles de predecir correctamente.

Teniendo en cuenta que es una proyección 3D de un espacio 8-dimensional (1 por característica), hace falta un estudio más exhaustivo de la distribución de los datos para extraer conclusiones.

A continuación se muestra la distribución de las muestras de cada etiqueta para cada característica.

In [31]:
features=[f'feature{i}' for i in range(1,9)]
trainplot=train.copy()
trainplot['target']=train['target'].astype(str)

for col in features:
    fig=px.histogram(data_frame=trainplot,x=col,color='target',category_orders={'target':['0','1','2']})
    fig.show()

A simple vista vemos que las distribuciones de las 3 etiquetas son diferentes en todas las características excepto en la 4, 7 y 8. Vamos a hacer un análisis más profundo calculando las medias y la desviación estándar de cada distribución.

In [33]:
featinfo=train.groupby(by='target').agg(['mean','std']).transpose()
featinfo['statvariance']=featinfo.apply(lambda x: variance([x[0],x[1],x[2]]),axis=1)

featinfo

target                0         1         2  statvariance
feature1 mean  1.000311 -0.997609 -0.996312      1.329699
         std   1.276897  1.224580  1.277883      0.000930
feature2 mean  1.032711 -0.991040 -0.038723      1.025075
         std   1.430708  1.021447  1.609550      0.090891
feature3 mean -1.006164 -1.021799  1.099521      1.489025
         std   1.057752  0.904074  1.309053      0.041796
feature4 mean -0.026314  0.067655  0.031604      0.002247
         std   1.491741  1.689426  1.451069      0.016258
feature5 mean -1.248619  0.355949  1.201771      1.549077
         std   1.567890  1.657338  1.123772      0.081656
feature6 mean  2.142814 -0.992432 -1.414459      3.777012
         std   1.685602  1.387680  1.063287      0.096877
feature7 mean -0.030125 -0.045520 -0.000289      0.000529
         std   1.035364  1.008968  1.002505      0.000303
feature8 mean  0.055401 -0.023712 -0.047069      0.002884
         std   0.993597  1.003256  1.012038      0.000085

Clasificación de las características por la variación de la media y la desviación típica de las distribuciones de las 3 etiquetas:

In [35]:
featquality=featinfo.reset_index().groupby(by='level_0').max()['statvariance'].sort_values(ascending=False)
featquality

level_0
feature6    3.777012
feature5    1.549077
feature3    1.489025
feature1    1.329699
feature2    1.025075
feature4    0.016258
feature8    0.002884
feature7    0.000529
Name: statvariance, dtype: float64

Vemos que para las caracterísisticas 1, 2, 3, 5 y 6 tienen grandes diferencias en la media tal como se intuía al ver las distribuciones anteriormente.

Sin embargo, a pesar de que en las características 4, 7 y 8 las distribuciones a simple vista parecían ser idénticas, vemos que en la 4 la desviación típica de la etiqueta 1 es algo más grande que las demás, así que puede aportar algo de información a la clasificación de las muestras.

Aún es pronto para descartar las etiquetas 7 y 8 de la predicción. Vamos a comprobar la relación directa de las variables 'malas' (4, 7 y 8) con las variables 'buenas' (el resto).

In [42]:
badf=['feature4','feature7','feature8']
goodf=[f for f in features if f not in worstf]
trainplot2=trainplot.melt(id_vars=goodf+['target'],value_vars=badf,var_name='feature',value_name='feature value')
for col in goodf:
    fig=px.scatter(data_frame=trainplot2,x=col,y='feature value',color='target',facet_col='feature',category_orders={'target':['0','1','2']})
    fig.show()

Comprobamos que la combinación de la característica 4 con alguna de las 'buenas' produce clusters más diferenciables que con las 7 y 8. De hecho, la diferenciación de los clusters para las 7 y 8 son prácticamente debidos a la diferenciación de las distribuciones de las variables 'buenas' correspondientes.

Finalmente vamos a entrenar el modelo random forest de scikit-learn por defecto y vamos a extraer la importancia de cada caracterísitica.

In [51]:
rf=RandomForestClassifier(random_state=2022)
rf.fit(X_train,y_train)

importances=pd.DataFrame()
importances['feature']=features
importances['importance']=rf.feature_importances_
importances.sort_values(by='importance',ascending=False)

feature  importance
5  feature6    0.240015
2  feature3    0.230123
1  feature2    0.163039
0  feature1    0.128038
4  feature5    0.108490
3  feature4    0.077179
6  feature7    0.027173
7  feature8    0.025944

Comprobamos que las 4, 7 y 8 son las peores, aunque la 4 aporta mucho más que la 7 y la 8, siendo comparable a la 5, la peor de las 'buenas', así que merece la pena conservarla.

# 2. Creación del modelo

El modelo es un algoritmo de random forests tuneado usando la función de exploración de hiperparámetros de scikit-learn. Además, se considera tanto el caso de mantener todas las variables o quitar la 7 y la 8. Para ello se añade una capa de preprocesamiento previa al clasificador. Las opciones son las siguientes:

- **Identity**: Transformador neutro. Deja pasar los datos sin ahcer nada.
```
class Identity(BaseEstimator, TransformerMixin):
    def __init__(self):
        pass  
    def fit(self, input_array, y=None):
        return self  
    def transform(self, input_array, y=None):
        return input_array*1
```
- **ColumnTransformer**: Elimina las características 7 y 8 y deja pasar el resto.
```
ColumnTransformer(transformers=[('dropfts','drop', ['feature7','feature8'])], remainder='passthrough')
```

Los hiperparámetros a explorar son los siguientes (valor por defecto en negrita):
- *n_estimators* (número de árboles): **100**, 150 o 200
- *min_samples_split* (nº mínimo de muestras requeridas para dividir un nodo interno): **2**, 3, 4 o 5
- *bootstrap* (usar en cada arbol solo una fracción aleatoria de los datos en vez de todos): **True** o False
- *class_weight* (considerar la fracción de cada etiqueta en el entrenamiento): 'balanced' o **None**

La exploración se efectúa con una validación cruzada con k=7.

*Para generar el modelo y la predicción se ha ejecutado app.py*

# 3. Resultados

A continuación se muestran los resultados de la exploración de hiperparámetros.

## 3.1 Top 10 modelos

In [67]:
pd.set_option('display.max_columns', None)
results=pd.read_csv(CV_RES_FILE)
results.fillna('None').drop('Unnamed: 0',axis=1).sort_values(by='rank_test_score').head(10)

mean_fit_time  std_fit_time  mean_score_time  std_score_time  \
50       0.395940      0.005243         0.013144        0.004109   
61       0.295175      0.006392         0.014147        0.006035   
51       0.195871      0.007483         0.010313        0.006649   
85       0.403055      0.006571         0.010810        0.008496   
63       0.199601      0.006013         0.009303        0.006564   
86       0.527277      0.007678         0.015723        0.000193   
79       0.404214      0.007248         0.013416        0.005477   
66       0.194822      0.006609         0.009355        0.006780   
48       0.201715      0.005045         0.005621        0.006894   
28       0.424140      0.000553         0.015718        0.000127   

                                            param_pre  param_rf__bootstrap  \
50  ColumnTransformer(remainder='passthrough',\n  ...                 True   
61  ColumnTransformer(remainder='passthrough',\n  ...                 True   
51  ColumnTransformer(remainder='passthrough',\n  ...                 True   
85  ColumnTransformer(remainder='passthrough',\n  ...                False   
63  ColumnTransformer(remainder='passthrough',\n  ...                 True   
86  ColumnTransformer(remainder='passthrough',\n  ...                False   
79  ColumnTransformer(remainder='passthrough',\n  ...                False   
66  ColumnTransformer(remainder='passthrough',\n  ...                 True   
48  ColumnTransformer(remainder='passthrough',\n  ...                 True   
28                                         Identity()                False   

   param_rf__class_weight  param_rf__min_samples_split  \
50               balanced                            2   
61                   None                            2   
51               balanced                            3   
85                   None                            2   
63                   None                            3   
86                   None                            2   
79               balanced                            4   
66                   None                            4   
48               balanced                            2   
28               balanced                            3   

    param_rf__n_estimators                                             params  \
50                     200  {'pre': ColumnTransformer(remainder='passthrou...   
61                     150  {'pre': ColumnTransformer(remainder='passthrou...   
51                     100  {'pre': ColumnTransformer(remainder='passthrou...   
85                     150  {'pre': ColumnTransformer(remainder='passthrou...   
63                     100  {'pre': ColumnTransformer(remainder='passthrou...   
86                     200  {'pre': ColumnTransformer(remainder='passthrou...   
79                     150  {'pre': ColumnTransformer(remainder='passthrou...   
66                     100  {'pre': ColumnTransformer(remainder='passthrou...   
48                     100  {'pre': ColumnTransformer(remainder='passthrou...   
28                     150  {'pre': Identity(), 'rf__bootstrap': False, 'r...   

    split0_test_score  split1_test_score  split2_test_score  \
50           0.920000           0.913333           0.940000   
61           0.920000           0.913333           0.940000   
51           0.920000           0.916667           0.940000   
85           0.916667           0.910000           0.933333   
63           0.920000           0.920000           0.940000   
86           0.910000           0.910000           0.936667   
79           0.916667           0.910000           0.936667   
66           0.926667           0.913333           0.940000   
48           0.916667           0.920000           0.940000   
28           0.916667           0.906667           0.933333   

    split3_test_score  split4_test_score  split5_test_score  \
50           0.923333           0.930000           0.903333   
61           0.916667           0.933333     

#### Top  10 capas de preprocesamiento de datos

In [105]:
results.fillna('None').drop('Unnamed: 0',axis=1).sort_values(by='rank_test_score').head(10)['param_pre'].reset_index(drop=True)

0    ColumnTransformer(remainder='passthrough',\n  ...
1    ColumnTransformer(remainder='passthrough',\n  ...
2    ColumnTransformer(remainder='passthrough',\n  ...
3    ColumnTransformer(remainder='passthrough',\n  ...
4    ColumnTransformer(remainder='passthrough',\n  ...
5    ColumnTransformer(remainder='passthrough',\n  ...
6    ColumnTransformer(remainder='passthrough',\n  ...
7    ColumnTransformer(remainder='passthrough',\n  ...
8    ColumnTransformer(remainder='passthrough',\n  ...
9                                           Identity()
Name: param_pre, dtype: object

Podemos observar que la decisión de eliminar las características 7 y 8 ha sido la correcta.

## 3.2 Mejor modelo

In [90]:
best_id=results.sort_values(by='rank_test_score').index[0]
param_cols=[col for col in results.columns if 'param_' in col]
results[param_cols].iloc[best_id]

param_pre                      ColumnTransformer(remainder='passthrough',\n  ...
param_rf__bootstrap                                                         True
param_rf__class_weight                                                  balanced
param_rf__min_samples_split                                                    2
param_rf__n_estimators                                                       200
Name: 50, dtype: object

In [101]:
score=results.iloc[best_id]['mean_test_score']
print(f'Puntuación media de la validación cruzada: {score}')

Puntuación media de la validación cruzada: 0.918095238095238


## 3.3 Visualización de la predicción

Finalmente vamos a hacer la misma visualización 3D que hemos hecho con el conjunto de entrenamiento con el conjunto de prueba junto a sus predicciones.

In [98]:
to3d=TSNE(n_components=3)

test3d=pd.DataFrame(to3d.fit_transform(X_test),columns=['x','y','z'])
test3d['target']=pd.read_csv(PRED_CSV_FILE).astype(str)

test3dplot=px.scatter_3d(test3d,x='x',y='y',z='z',color='target',category_orders={'target':['0','1','2']})

test3dplot

Vemos los mismos 3 clusters marcados aunque con menos intersección, ya que la predicción se basa en los datos de entrenamiento más similares. De todas maneras, la proyección 3D es muy similar a lo visto con los datos de entrenamiento, así que la precisión debería de ser buena, como ya ha indicado la puntuación de la validación cruzada de la exploración de hiperparámetros.